In [1]:
import os
import string
import unicodedata
import nltk
import spacy
import gensim
import requests
import hdbscan
import numpy as np
import re
import hdbscan

from sklearn.metrics.pairwise import cosine_similarity
from nltk.corpus import stopwords, wordnet
from nltk.stem import WordNetLemmatizer
from gensim import corpora
from gensim.models import LdaModel, CoherenceModel
from nltk.tokenize import word_tokenize, sent_tokenize
from nltk.collocations import BigramCollocationFinder, BigramAssocMeasures, TrigramCollocationFinder, TrigramAssocMeasures
from nltk import pos_tag
from nltk.util import ngrams
from collections import Counter, defaultdict
from sentence_transformers import SentenceTransformer


d:\Python\Python312\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# Load NLP Models
spacy_nlp = spacy.load("en_core_web_sm")
#embedding_model = SentenceTransformer("all-MiniLM-L6-v2") faster
embedding_model = SentenceTransformer("all-mpnet-base-v2") 
stop_words = set(stopwords.words("english"))

# Fetch stopwords
def fetch_stopwords_from_github(url):
    response = requests.get(url)
    return set(response.text.splitlines())

github_stopwords_url = 'https://raw.githubusercontent.com/stopwords-iso/stopwords-en/master/stopwords-en.txt'
github_stopwords = fetch_stopwords_from_github(github_stopwords_url)

stop_words = set(stopwords.words('english'))
custom_stop_words = ['like', 'yeah', 'know', 'um', 'uh', 'really', 'one', 'go', 'right', 'okay', 'well', 'said', 
                    'going', 'got', 'na', 'always', 'every', 'each', 'say', 'el', 'little', 'still', 
                    'best', 'dutch', 'nice', 'great', 'awesome', 'good', 'cool', 'love', 'amazing', 'wow',
                    'breaking news', 'report', 'coverage', 'investigation', 'interview', 'documentary', 'news', 'netherlands', 'psy', 'subtitle', 'description', 'link', 
                    'journalist', 'headline', 'reporter', 'current events', 'special report', 
                    'analysis', 'documented', 'broadcast', 'reporting', 'v', 'food', 'travel', 'react', 
                    'reacts', 'reaction', 'foreigner', 'thing', 'visit', 'dc', 'japan', 'first', 'fast', 
                    'asia', 'ang', 'indian', 'thai', 'vietnamese', 'russia', 'gon', 'canada', 'canadian', 'russian', 
                    'russia', 'guy', 'lot', 'bit', 'diba', 'ola', 'cuz', 'thai', 'thailand', 'person', 'citizen', 'foreigner', 'foreign', 'foreigners',
                    'facebook', 'filipinos', 'filipinas', 'vlog', 'vlogs', 'vlogging', 'hashtag', 'india', 'bro', 'dito', 'people', 'time', 'music', 'gonna', 'life', 
                    'lol', 'guys', 'tho', 'cute', 'hmm', 'huh', 'channel', 'subscribe', 'day6', 'mandarin', 'chinese', 'beautiful',
                    'chuckles', 'fbe', 'hit', 'laughs', 'yo', 'ka', 'word', 'living', 'boi', 'minimum', 'ya', 'successful', 'perfectly', 'yeap', 
                    'wondering', 'fantastic', 'hurry', 'german', 'age', 'country', 'subscribing', 'bluesy', 'jump', 'pretty', 'understanding', 'personalized',
                    'and', 'the', 'to', 'of', 'in', 'for', 'on', 'with', 'at', 'by', 'from', 'up', 'about', 'over', 'into', 'through', 'between', 'under', 'against', 'all',
                    'you', 'haha', 'hahaha', 'ha', 'hey', 'bye', 'hello', 'hi', 'oh', 'blah', 'easy', 'alright', 'ta', 'day', 'ooh', 'en', 'do', 'lot', 'comment', 'notification', 
                    'korean', 'jjajangmyeon', 'jajangmyeon', 'damn', 'yall', 'month', 'week', 'year', 'ohhh', 'pvf', 'dude', 'mmm', 'kagilagilalas', 'ofcourse', 'australia', 'uxo', 
                    'atleast', 'yusuf', 'bangkok', 'ot', 'anytime', 'allover', 'kala', 'nope', 'wan', 'brazil', 'smooth', 'ot', 'timeshere', 'batchof', 'yep', 'opo', 'del',
                    'gosh', 'po', 'ourself', 'wo', 'wait', 'ugh', 'nyc', 'whoa', 'nicaragua', 'yup', 'em', 'bout', 'le', 'omg', 'overwhelm', 'maam', 'nicer', 'haha', 'hahaha', 'ha', 
                    'nbcs', 'lana', 'rc', 'whatsoever', 'oxy', 'decade', 'whyd', 'unknown', 'ahhhhh', 'ohoh', 'ohto', 'ohhhh', 'bruh', 'ooe', 'ahmedabad', 'mexico', 
                    'understand', 'excuse', 'kinda', 'applause', 'oooh', 'thiswhat', 'nevermind', 'ahh', 'againthank', 'toto', 'aww', 'nah', 'bbmas', 'ay', 'op', 'huh', 'huhu',
                    'tada', 'beacuse', 'voila', 'upstairs', 'thatswhy', 'yea', 'that', 'armenia', 'or', 'not', 'funwhat', 'aka', 'armeniathat', 'woosexy', 'worth', 'laugh', 'box', 
                    'xd', 'vb', 'eff', 'ananya', 'welsh', 'latron', 'shout', 'whatwhat', 'what', 'pause', 'why', 'thats', 'byebye', 'iv', 'bye', 'ado', 'ownup', 'dom', 'jomm', 'sir', 
                    'budgie', 'nomac', 'lavocha', 'germany', 'why', 'walang', 'superduper', 'philip', 'mom', 'jre', 'giddy', 'intro', 'dupe', 'europe', 'dream', 'team', 'dislike', 'content', 
                    'yoongi', 'royale', 'ilu', 'jhope', 'day', 'jin', 'ecc', 'nyhs', 'nego', 'chavez', 'pb', 'everyones', 'epic', 'matter', 'oneonone', 'region', 'change', 'ho', 'seetoh', 
                    'atin', 'vpn', 'facetune', 'busu', 'mackie', 'clyd', 'china', 'rest', 'friend', 'woah', 'dindins', 'poster', 'vibe', 'woman', 'boss', 'woah', 'type', 'mahana', 'joke', 
                    'taller', 'insane', 'whang', 'psa', 'manatee', 'recommend', 'caesar', 'mmmhmm', 'mosul', 'dun', 'clue', 'naysayer', 'hindi', 'ko', 'pero', 'bulgaria', 'question', 'video', 
                    'yobi', 'hindu', 'expat', 'option', 'gap', 'eu', 'simo', 'kouignamann', 'bct', 'month', 'cfo', 'philippines', 'philippine', 'british', 'filipino', 'video', 
                    'http', 'korea', 'korean', 'youtube', 'google', 'united', 'america', 'american', 'kpop', '필리핀', 'bts', 'blackpink', 'twice', 'exo', 'k-pop', 
                    'seventeen', 'stray kids', 'nct', 'kdrama', 'aespa', 'taehyung', 'jimin', 'jungkook']
stop_words.update(custom_stop_words, github_stopwords)

lemmatizer = WordNetLemmatizer()

# Folder paths
transcripts_folder_path = 'standard_dataset/'
tags_folder_path = 'tags/'

# Function to load video tags only for fetched video IDs
def load_video_tags(folder_path, video_ids):
    video_tags = {}
    for video_id in video_ids:
        tag_file = os.path.join(folder_path, f"{video_id}.txt")
        if os.path.exists(tag_file):
            with open(tag_file, "r", encoding="utf-8") as file:
                tags_content = file.read().lower()
                video_tags[video_id] = tags_content.split()  # Store as list of words
        else:
            video_tags[video_id] = []  # Default to empty list if no tags
    return video_tags

video_ids = []
transcript_files = []
for file_name in os.listdir(transcripts_folder_path):
    if file_name.endswith('.txt'):
        video_id = file_name.split('_captions')[0]
        video_ids.append(video_id)
        transcript_files.append((video_id, file_name)) 

video_tags = load_video_tags(tags_folder_path, video_ids)

d:\Python\Python312\Lib\site-packages\spacy\util.py:910: UserWarning: [W095] Model 'en_core_web_sm' (3.7.1) was trained with spaCy v3.7.2 and may not be 100% compatible with the current version (3.8.4). If you see errors or degraded performance, download a newer compatible model or retrain your custom model with the current spaCy version. For more details and available updates, run: python -m spacy validate
  warnings.warn(warn_msg)


In [3]:
def is_latin_script(word):
    return all('LATIN' in unicodedata.name(char, '') or char.isdigit() for char in word)

# Function to detect both bigram and trigram collocations
def detect_collocations(tokens, min_freq=3):
    bigram_measures = BigramAssocMeasures()
    trigram_measures = TrigramAssocMeasures()

    # Find bigrams
    bigram_finder = BigramCollocationFinder.from_words(tokens)
    bigram_finder.apply_freq_filter(min_freq)
    bigrams = set(['_'.join(bigram) for bigram in bigram_finder.nbest(bigram_measures.pmi, 10)])

    # Find trigrams
    trigram_finder = TrigramCollocationFinder.from_words(tokens)
    trigram_finder.apply_freq_filter(min_freq)
    trigrams = set(['_'.join(trigram) for trigram in trigram_finder.nbest(trigram_measures.pmi, 10)])

    return bigrams, trigrams


def segment_text(text):
    sentences = sent_tokenize(text)
    
    if len(sentences) < 2:
        return [text]

    # Encode sentences into embeddings
    sentence_embeddings = embedding_model.encode(sentences, normalize_embeddings=True)  # ✅ Normalize embeddings

    cosine_sim_matrix = cosine_similarity(sentence_embeddings)

    # Convert similarity to distance 
    distance_matrix = np.array(1 - cosine_sim_matrix, dtype=np.float64)  

    cluster_model = hdbscan.HDBSCAN(
        min_cluster_size=2,      
        min_samples=1,           
        metric="precomputed"    
    )

    clusters = cluster_model.fit_predict(distance_matrix)

    # Group sentences by cluster
    segmented_text = defaultdict(list)
    unclustered = []

    for i, cluster in enumerate(clusters):
        if cluster != -1:
            segmented_text[cluster].append(sentences[i])
        else:
            unclustered.append(sentences[i]) 

    if not segmented_text:
        return [text]

    # Merge unclustered sentences into the nearest cluster
    if unclustered:
        largest_cluster = max(segmented_text, key=lambda k: len(segmented_text[k]))
        segmented_text[largest_cluster].extend(unclustered)

    # Preserve sentence order
    sorted_segments = sorted(segmented_text.items(), key=lambda x: min([sentences.index(s) for s in x[1]]))

    return [' '.join(segment) for _, segment in sorted_segments]


def preprocess_text(doc, video_id, tag_weight=2, ngram_weight_factor=2):
    # Segment the text into meaningful chunks
    doc = re.sub(r'([a-zA-Z]+)[,;:!?.]', r'\1', doc)
    segmented_text = segment_text(doc)
    
    processed_segments = []
    
    for segment in segmented_text:
        segment = segment.lower().translate(str.maketrans('', '', string.punctuation))
        tokens = word_tokenize(segment)

        # Remove stopwords
        tokens = [word for word in tokens if word not in stop_words and word.isalpha() and is_latin_script(word)]

        # Detect meaningful bigram and trigram collocations
        bigrams, trigrams = detect_collocations(tokens)

        # Generate n-grams (both bigrams and trigrams)
        bigram_tokens = ['_'.join(gram) for gram in ngrams(tokens, 2)]
        trigram_tokens = ['_'.join(gram) for gram in ngrams(tokens, 3)]

        # Count n-gram frequency
        bigram_frequencies = Counter(bigram_tokens)
        trigram_frequencies = Counter(trigram_tokens)

        # Merge n-grams into single tokens
        merged_tokens = []
        i = 0
        while i < len(tokens) - 2:  # Check for trigrams first
            trigram = f"{tokens[i]}_{tokens[i+1]}_{tokens[i+2]}"
            bigram = f"{tokens[i]}_{tokens[i+1]}"

            if trigram in trigrams:
                merged_tokens.append(trigram)
                i += 3  # Skip next two words since it's part of the trigram
            elif bigram in bigrams:
                merged_tokens.append(bigram)
                i += 2  # Skip next word since it's part of the bigram
            else:
                merged_tokens.append(tokens[i])
                i += 1

        # Append any remaining words
        while i < len(tokens):
            merged_tokens.append(tokens[i])
            i += 1

        # POS tagging
        tokens_with_pos = pos_tag(merged_tokens)

        # Apply lemmatization
        lemmatized_tokens = [lemmatizer.lemmatize(word, get_wordnet_pos(pos)) for word, pos in tokens_with_pos]

        # Assign weight based on n-gram occurrence
        weighted_tokens = []
        for token in lemmatized_tokens:
            if token in trigram_frequencies:
                token_weight = 1 + trigram_frequencies[token] * ngram_weight_factor  
            elif token in bigram_frequencies:
                token_weight = 1 + bigram_frequencies[token] * (ngram_weight_factor - 1)  
            else:
                token_weight = 1
            weighted_tokens.extend([token] * int(token_weight))

        # Include video tags
        if video_id in video_tags:
            tags = video_tags[video_id]
            for tag in tags:
                if tag.isalpha():
                    weighted_tokens.extend([tag] * int(tag_weight))

        processed_segments.append(' '.join(weighted_tokens))
    
    return ' '.join(processed_segments), segmented_text



def get_wordnet_pos(treebank_tag):
    """Convert POS tag to WordNet format for lemmatization."""
    if treebank_tag.startswith('J'):
        return wordnet.ADJ
    elif treebank_tag.startswith('V'):
        return wordnet.VERB
    elif treebank_tag.startswith('N'):
        return wordnet.NOUN
    elif treebank_tag.startswith('R'):
        return wordnet.ADV
    else:
        return wordnet.NOUN  # Default to noun

In [4]:
all_documents = []
all_segments = []  # To store segments for each document
preprocessed_text = []

for video_id, file_name in transcript_files:
    with open(os.path.join(transcripts_folder_path, file_name), 'r', encoding='utf-8') as file:
        content = file.read().lower()
        if len(content.split()) >= 100: 
            processed_text, segments = preprocess_text(content, video_id)  # Get both processed text and segments
            preprocessed_text.append((video_id, processed_text))
            all_documents.append(processed_text)
            all_segments.append((video_id, segments))  # Store segments with video ID

for video_id, segments in all_segments:
    print(f"\nVideo ID: {video_id}")
    for i, segment in enumerate(segments, 1):
        print(f"Segment {i}: {segment}")
# Create Dictionary and Corpus
dictionary = corpora.Dictionary([doc.split() for doc in all_documents])
corpus = [dictionary.doc2bow(doc.split()) for doc in all_documents]


Video ID: --8n6A8Q6M0_$200 Luxury Beach Hotel in The Philippines ðŸ‡µðŸ‡­
Segment 1: oh my god
it is just the perfect recipe for a good day
want some beer
sure
oh it's big bottle
oh my goodness
three tarzan
good morning from bohol here in the philippines
everybody guys this look
how gorgeous this place is
crystal clear water
it's just honestly such a vibe perfect
temperature to be spending the day by the beach
and that is exactly what we're gonna do
today because i'm staying about 200 meters
up that way at a $200 per night hotel
on there for the next couple of nights
and i arrived in the uh last night
uh it was raining
it was kind of a little bit miserable
so i was like you know what
we'll wait until the weather is good and boy
or boy did the weather turn out good today
this water guys if you know me i'm australian
i live in sydney
i live by the beach and i absolutely
love being by the beaches
so it is just absolute paradise right
here right by the beach uh the hotel
super nice room o

In [5]:
for video_id, document in preprocessed_text:
    print(f"\nVideo ID: {video_id}")
    print(f"Preprocessed Document: {document}")


Video ID: --8n6A8Q6M0_$200 Luxury Beach Hotel in The Philippines ðŸ‡µðŸ‡­
Preprocessed Document: god perfect recipe beer bottle goodness tarzan morning bohol gorgeous crystal water honestly perfect temperature spending beach stay meter night hotel couple night arrive night rain miserable weather boy boy weather water australian live sydney live beach absolutely beach absolute paradise beach hotel super overlook water mall kayak paddle_boarding paddle_boarding paddle_boarding paddle_boarding paddle board beach tide tide walk basically boats couple hour beach expand enjoy luxury bring_journey bring_journey bring_journey bring_journey tara explore luxury hotel cebu night cent photo shoot hotel set cameras pool dlsr dlsr dlsr gopro hotel plenty kayak paddle board hotel beach private access guest kayak whatnot kayak hot modala beach resort head honestly super hot perfect swim head pool even arrive walk walk strip mall restaurant stuff entrance beach entrance palm_tree palm_tree ocean mount

In [6]:
# Train LDA Model
lda_model = LdaModel(corpus, num_topics=10, id2word=dictionary, alpha='auto', eta='symmetric', passes=100)

# Compute Coherence Score
coherence_model = CoherenceModel(model=lda_model, corpus=corpus, dictionary=dictionary, coherence='u_mass')
coherence_score = coherence_model.get_coherence()
print(f"Coherence Score: {coherence_score}")

# Print Topics
topics = lda_model.print_topics(num_words=20)
for topic_id, topic_words in topics:
    print(f"Topic {topic_id}: {topic_words}")

Coherence Score: -10.684854719177029
Topic 0: 0.018*"whale_shark" + 0.012*"fried_chicken" + 0.010*"whale_sharks" + 0.007*"manila" + 0.006*"eat" + 0.005*"ice_cream" + 0.005*"ferris_wheel" + 0.005*"spanish" + 0.005*"sauce" + 0.005*"sweet" + 0.005*"walk" + 0.005*"city" + 0.005*"global_global_global" + 0.004*"dessert" + 0.004*"chicken" + 0.004*"restaurant" + 0.004*"check" + 0.004*"rice" + 0.004*"dish" + 0.004*"taste"
Topic 1: 0.008*"beach" + 0.006*"keith_sara" + 0.005*"hotel" + 0.005*"water" + 0.005*"eat" + 0.004*"super" + 0.004*"walk" + 0.004*"rice" + 0.004*"bum_gun" + 0.004*"feel" + 0.004*"head" + 0.004*"start" + 0.004*"god" + 0.004*"perfect" + 0.004*"stay" + 0.004*"chicken" + 0.003*"hard" + 0.003*"minute" + 0.003*"tnt_boys" + 0.003*"chicken_joy"
Topic 2: 0.018*"chocolate_hills" + 0.017*"pizza_hut" + 0.016*"avoid_scammed_broken" + 0.015*"tiger_sugar" + 0.012*"fried_chicken" + 0.009*"eat" + 0.009*"stay_tuned" + 0.009*"med_school" + 0.006*"pork_belly" + 0.006*"rain" + 0.005*"pizza" + 0.005

In [7]:
for idx, doc_bow in enumerate(corpus):
    video_id = video_ids[idx]
    topic_distribution = lda_model.get_document_topics(doc_bow, minimum_probability=0)
    dominant_topic = sorted(topic_distribution, key=lambda x: x[1], reverse=True)[0]  # Highest probability
    print(f"Video {video_id}: Dominant Topic {dominant_topic[0]} with probability {dominant_topic[1]:.4f}")


Video --8n6A8Q6M0_$200 Luxury Beach Hotel in The Philippines ðŸ‡µðŸ‡­: Dominant Topic 1 with probability 1.0000
Video 0IMWasj76yU_Philippines Army vs Thailand Army: Dominant Topic 7 with probability 0.9997
Video 1kErCqgIVMk_Tour of The House We Built in The Philippines: Dominant Topic 3 with probability 0.9998
Video 2ftG8JuMzz4_Top 5 Exotic Foods in the Philippines The BRAVE MUST TRY!: Dominant Topic 7 with probability 0.9998
Video 2TmagN6RhkI_VOCAL COACH REACTS - REGINE VELASQUEZ - Araw-Gabi: Dominant Topic 1 with probability 0.9996
Video 3n1nspLgfd4_Balut!!!!! - Manila, Philippines - Now United: Dominant Topic 7 with probability 0.3833
Video 401ZvQ11euA_Did China Buy the Philippines With False Investment Promises: Dominant Topic 0 with probability 0.9998
Video 4OiOwDh5lKE_Chef Kuya Joey Is Flying To The Philippines!  ðŸ‡µðŸ‡­: Dominant Topic 1 with probability 0.5990
Video 6ftiWoCJ4dM_Filipino Food In The Netherlands  Cafe Nordrick!!: Dominant Topic 1 with probability 0.9987
Video 7j

In [8]:
from collections import defaultdict

# Dictionary to store the count of videos per topic
topic_video_count = defaultdict(int)

# Mapping of video ID to its dominant topic
video_topic_mapping = {}

for idx, doc_bow in enumerate(corpus):
    video_id = video_ids[idx]  # Get video ID
    topic_distribution = lda_model.get_document_topics(doc_bow, minimum_probability=0)

    # Get the most dominant topic (highest probability)
    dominant_topic = sorted(topic_distribution, key=lambda x: x[1], reverse=True)[0][0]
    
    # Store the mapping
    video_topic_mapping[video_id] = dominant_topic
    
    # Increase count for that topic
    topic_video_count[dominant_topic] += 1

# Print number of videos assigned to each topic
print("\nNumber of Videos per Topic:")
for topic, count in sorted(topic_video_count.items()):
    print(f"Topic {topic}: {count} videos")



Number of Videos per Topic:
Topic 0: 13 videos
Topic 1: 15 videos
Topic 2: 10 videos
Topic 3: 8 videos
Topic 4: 7 videos
Topic 5: 7 videos
Topic 6: 6 videos
Topic 7: 15 videos
Topic 8: 10 videos
Topic 9: 9 videos


In [9]:
topic_to_videos = defaultdict(list)

video_topic_mapping = {}

# probability threshold for assigning multiple topics
prob_threshold = 0.2

# Dictionary to store topic words for each video
video_topic_words_LDA1 = {}

for idx, doc_bow in enumerate(corpus):
    video_id = video_ids[idx]  # Get video ID
    topic_distribution = lda_model.get_document_topics(doc_bow, minimum_probability=0)

    # Get topics where probability is above threshold
    assigned_topics = [topic for topic, prob in topic_distribution if prob >= prob_threshold]
    video_topic_mapping[video_id] = assigned_topics  # Store assigned topics per video

    for topic in assigned_topics:
        topic_to_videos[topic].append(video_id)

    # Get the representative words for each assigned topic
    topic_words = []
    for topic in assigned_topics:
        words = [word for word, _ in lda_model.show_topic(topic, topn=10)]  # Get top 10 words
        topic_words.append(", ".join(words))  # Convert list to string

    # Store the topic words as a string
    video_topic_words_LDA1[video_id] = "; ".join(topic_words)  # Separate topics with `;`

# Count occurrences of each topic
topic_counts = Counter()

for topics in video_topic_mapping.values():
    for topic in topics:
        topic_counts[topic] += 1

# Print the number of videos per topic
print("\nNumber of Videos Per Topic:")
for topic, count in sorted(topic_counts.items()):
    print(f"Topic {topic}: {count} videos")

# Print topics assigned per video
print("\nTopics Assigned Per Video:")
for video_id, topics in video_topic_mapping.items():
    topic_list = ', '.join(map(str, topics)) if topics else "No dominant topic"
    print(f"Video ID: {video_id} → Topics: {topic_list}")

# Print videos per topic
print("\nTop Words Per Topic:")
num_words = 30  

for topic_id in sorted(topic_to_videos.keys()): 
    top_words = lda_model.show_topic(topic_id, num_words)
    words_str = ', '.join([word for word, prob in top_words])
    print(f"Topic {topic_id}: {words_str}")



Number of Videos Per Topic:
Topic 0: 13 videos
Topic 1: 16 videos
Topic 2: 14 videos
Topic 3: 10 videos
Topic 4: 8 videos
Topic 5: 9 videos
Topic 6: 8 videos
Topic 7: 15 videos
Topic 8: 11 videos
Topic 9: 9 videos

Topics Assigned Per Video:
Video ID: --8n6A8Q6M0_$200 Luxury Beach Hotel in The Philippines ðŸ‡µðŸ‡­ → Topics: 1
Video ID: 0IMWasj76yU_Philippines Army vs Thailand Army → Topics: 7
Video ID: 1kErCqgIVMk_Tour of The House We Built in The Philippines → Topics: 3
Video ID: 2ftG8JuMzz4_Top 5 Exotic Foods in the Philippines The BRAVE MUST TRY! → Topics: 7
Video ID: 2TmagN6RhkI_VOCAL COACH REACTS - REGINE VELASQUEZ - Araw-Gabi → Topics: 1
Video ID: 3n1nspLgfd4_Balut!!!!! - Manila, Philippines - Now United → Topics: 2, 7, 8
Video ID: 401ZvQ11euA_Did China Buy the Philippines With False Investment Promises → Topics: 0
Video ID: 4OiOwDh5lKE_Chef Kuya Joey Is Flying To The Philippines!  ðŸ‡µðŸ‡­ → Topics: 1, 5
Video ID: 6ftiWoCJ4dM_Filipino Food In The Netherlands  Cafe Nordrick!! → 

In [10]:
# Dictionary to store LDA2 topic words for each video
video_topics = {}
video_topic_words_lda2 = {}
video_segments = {}  # To store segments for each video

# Create a global dictionary for LDA
dictionary = corpora.Dictionary()

# Process each video
for video_id, file_name in transcript_files:
    with open(os.path.join(transcripts_folder_path, file_name), 'r', encoding='utf-8') as file:
        content = file.read().lower()
        
        if len(content.split()) >= 100:  
            # Preprocess text and get segments
            processed_text, segments = preprocess_text(content, video_id)
            
            # Store segments for the video
            video_segments[video_id] = segments
            
            # Create Dictionary and Corpus
            tokens = processed_text.split()
            dictionary.add_documents([tokens])  # Update global dictionary
            corpus = [dictionary.doc2bow(tokens)]
            
            # Train LDA Model
            num_topics = 3  # Limit topics to at most 5 or vocab size
            lda_model_2 = LdaModel(corpus, num_topics=num_topics, id2word=dictionary, alpha='auto', eta='symmetric', passes=100)
            
            # Compute Coherence Score
            coherence_model = CoherenceModel(model=lda_model_2, corpus=corpus, dictionary=dictionary, coherence='u_mass')
            coherence_score = coherence_model.get_coherence()
            
            # Get topic distribution for the video
            topic_distribution = lda_model_2.get_document_topics(corpus[0], minimum_probability=0)
            assigned_topics = {topic: prob for topic, prob in topic_distribution if prob > 0.5}  # Threshold for multiple topics
            
            # Store video topic info
            video_topics[video_id] = {
                "topics": assigned_topics,
                "top_words": {i: lda_model_2.show_topic(i, 20) for i in range(num_topics)},
                "coherence": coherence_score
            }

# Populate video_topic_words_lda2
for video_id, data in video_topics.items():
    topic_words = []
    
    for topic_id, prob in data["topics"].items():
        words = [word for word, _ in data["top_words"][topic_id]]  # Extract top words
        topic_words.append(", ".join(words))  # Convert list to string

    # Store the topic words as a string
    video_topic_words_lda2[video_id] = "; ".join(topic_words)  # Separate topics with `;`

# Print topics per video
for video_id, data in video_topics.items():
    print(f"\nVideo ID: {video_id}")
    print(f"Coherence Score: {data['coherence']:.4f}")
    print("Assigned Topics:")
    for topic_id, prob in data["topics"].items():
        print(f"  Topic {topic_id} ({prob:.2f} probability): {[word for word, _ in data['top_words'][topic_id]]}")
    
    # Display segments for the video
    print("\nSegments:")
    for i, segment in enumerate(video_segments[video_id], 1):
        print(f"Segment {i}: {segment}")


Video ID: --8n6A8Q6M0_$200 Luxury Beach Hotel in The Philippines ðŸ‡µðŸ‡­
Coherence Score: 0.0000
Assigned Topics:
  Topic 1 (1.00 probability): ['beach', 'bum_gun', 'hotel', 'water', 'rainy_season', 'jet', 'god', 'super', 'perfect', 'ski', 'head', 'stay', 'walk', 'hour', 'sand', 'bed', 'tide', 'couple', 'fun', 'margarita']

Segments:
Segment 1: oh my god
it is just the perfect recipe for a good day
want some beer
sure
oh it's big bottle
oh my goodness
three tarzan
good morning from bohol here in the philippines
everybody guys this look
how gorgeous this place is
crystal clear water
it's just honestly such a vibe perfect
temperature to be spending the day by the beach
and that is exactly what we're gonna do
today because i'm staying about 200 meters
up that way at a $200 per night hotel
on there for the next couple of nights
and i arrived in the uh last night
uh it was raining
it was kind of a little bit miserable
so i was like you know what
we'll wait until the weather is good and bo

In [11]:
# K-Means Segmentation
def segment_text_kmeans(doc, max_segments=10):
    sentences = sent_tokenize(doc)
    
    if len(sentences) <= 1:
        return [doc]
    
    # Generate sentence embeddings with normalization
    sentence_embeddings = embedding_model.encode(sentences, normalize_embeddings=True)

    # Determine the number of segments (ensure it's valid)
    num_segments = min(max_segments, len(sentences) // 2) 

    # Perform K-means clustering with cosine distance
    kmeans = KMeans(n_clusters=num_segments, random_state=42, n_init=10)
    clusters = kmeans.fit_predict(sentence_embeddings)

    # Group sentences by cluster
    segmented_text = []
    for cluster_id in range(num_segments):
        cluster_sentences = [sentence for sentence, cluster in zip(sentences, clusters) if cluster == cluster_id]
        if cluster_sentences:  # ✅ Avoid empty clusters
            segmented_text.append(' '.join(cluster_sentences))
    
    return segmented_text

transcript_files = []
for file_name in os.listdir(transcripts_folder_path):
    if file_name.endswith('.txt'):
        video_id = file_name.split('_captions')[0]
        video_ids.append(video_id)
        transcript_files.append((video_id, file_name)) 

video_tags = load_video_tags(tags_folder_path, video_ids)

all_documents = []
all_segments = []  # To store segments for each document

for video_id, file_name in transcript_files:
    with open(os.path.join(transcripts_folder_path, file_name), 'r', encoding='utf-8') as file:
        content = file.read().lower()
        if len(content.split()) >= 100: 
            processed_text, segments = preprocess_text(content, video_id)  # Get both processed text and segments
            all_documents.append(processed_text)
            all_segments.append((video_id, segments))  # Store segments with video ID

# Display segments for each document
print("\nSegments per Document:")
for video_id, segments in all_segments:
    print(f"\nVideo ID: {video_id}")
    for i, segment in enumerate(segments, 1):
        print(f"Segment {i}: {segment}")


Segments per Document:

Video ID: --8n6A8Q6M0_$200 Luxury Beach Hotel in The Philippines ðŸ‡µðŸ‡­
Segment 1: oh my god
it is just the perfect recipe for a good day
want some beer
sure
oh it's big bottle
oh my goodness
three tarzan
good morning from bohol here in the philippines
everybody guys this look
how gorgeous this place is
crystal clear water
it's just honestly such a vibe perfect
temperature to be spending the day by the beach
and that is exactly what we're gonna do
today because i'm staying about 200 meters
up that way at a $200 per night hotel
on there for the next couple of nights
and i arrived in the uh last night
uh it was raining
it was kind of a little bit miserable
so i was like you know what
we'll wait until the weather is good and boy
or boy did the weather turn out good today
this water guys if you know me i'm australian
i live in sydney
i live by the beach and i absolutely
love being by the beaches
so it is just absolute paradise right
here right by the beach uh the

In [12]:
# Create Dictionary and Corpus for LDA
dictionary = corpora.Dictionary([doc.split() for doc in all_documents])
corpus = [dictionary.doc2bow(doc.split()) for doc in all_documents]

# Train LDA model
lda_model = LdaModel(corpus, num_topics=10, id2word=dictionary, alpha='auto', eta='symmetric', passes=100)

# Compute coherence score
coherence_model = CoherenceModel(model=lda_model, corpus=corpus, dictionary=dictionary, coherence='u_mass')
coherence_score = coherence_model.get_coherence()

print(f"Coherence Score: {coherence_score}")

for idx, doc_bow in enumerate(corpus):
    video_id = video_ids[idx]  
    topic_distribution = lda_model.get_document_topics(doc_bow, minimum_probability=0)
    print(f"Video {video_id}: {topic_distribution}")

topics = lda_model.print_topics(num_words=20) 
for topic_id, topic_words in topics:
    print(f"Topic {topic_id}: {topic_words}")


Coherence Score: -9.207156305982911
Video --8n6A8Q6M0_$200 Luxury Beach Hotel in The Philippines ðŸ‡µðŸ‡­: [(0, 8.446834e-06), (1, 6.758094e-06), (2, 7.759307e-06), (3, 2.9677792e-06), (4, 4.580904e-06), (5, 3.9662827e-06), (6, 6.4441238e-06), (7, 2.7311708e-06), (8, 5.4089705e-06), (9, 0.99995095)]
Video 0IMWasj76yU_Philippines Army vs Thailand Army: [(0, 5.96858e-05), (1, 4.7753074e-05), (2, 5.48277e-05), (3, 2.0970494e-05), (4, 0.9996495), (5, 2.8025976e-05), (6, 4.553454e-05), (7, 1.9298606e-05), (8, 3.822009e-05), (9, 3.6220612e-05)]
Video 1kErCqgIVMk_Tour of The House We Built in The Philippines: [(0, 3.3538e-05), (1, 0.99981165), (2, 3.0808184e-05), (3, 1.17835125e-05), (4, 1.8188393e-05), (5, 1.5748052e-05), (6, 2.5586274e-05), (7, 1.0844063e-05), (8, 2.1476217e-05), (9, 2.0352692e-05)]
Video 2ftG8JuMzz4_Top 5 Exotic Foods in the Philippines The BRAVE MUST TRY!: [(0, 2.7694006e-05), (1, 2.2157263e-05), (2, 2.5439864e-05), (3, 9.730237e-06), (4, 0.99983734), (5, 1.3003956e-05), 

In [13]:
for idx, doc_bow in enumerate(corpus):
    video_id = video_ids[idx]
    topic_distribution = lda_model.get_document_topics(doc_bow, minimum_probability=0)
    dominant_topic = sorted(topic_distribution, key=lambda x: x[1], reverse=True)[0]  # Highest probability
    print(f"Video {video_id}: Dominant Topic {dominant_topic[0]} with probability {dominant_topic[1]:.4f}")


Video --8n6A8Q6M0_$200 Luxury Beach Hotel in The Philippines ðŸ‡µðŸ‡­: Dominant Topic 9 with probability 1.0000
Video 0IMWasj76yU_Philippines Army vs Thailand Army: Dominant Topic 4 with probability 0.9996
Video 1kErCqgIVMk_Tour of The House We Built in The Philippines: Dominant Topic 1 with probability 0.9998
Video 2ftG8JuMzz4_Top 5 Exotic Foods in the Philippines The BRAVE MUST TRY!: Dominant Topic 4 with probability 0.9998
Video 2TmagN6RhkI_VOCAL COACH REACTS - REGINE VELASQUEZ - Araw-Gabi: Dominant Topic 1 with probability 0.9996
Video 3n1nspLgfd4_Balut!!!!! - Manila, Philippines - Now United: Dominant Topic 1 with probability 0.5363
Video 401ZvQ11euA_Did China Buy the Philippines With False Investment Promises: Dominant Topic 3 with probability 0.9998
Video 4OiOwDh5lKE_Chef Kuya Joey Is Flying To The Philippines!  ðŸ‡µðŸ‡­: Dominant Topic 2 with probability 0.9994
Video 6ftiWoCJ4dM_Filipino Food In The Netherlands  Cafe Nordrick!!: Dominant Topic 3 with probability 0.9986
Video 7j

In [14]:
from collections import defaultdict

# Dictionary to store the count of videos per topic
topic_video_count = defaultdict(int)

# Mapping of video ID to its dominant topic
video_topic_mapping = {}

for idx, doc_bow in enumerate(corpus):
    video_id = video_ids[idx]  # Get video ID
    topic_distribution = lda_model.get_document_topics(doc_bow, minimum_probability=0)

    # Get the most dominant topic (highest probability)
    dominant_topic = sorted(topic_distribution, key=lambda x: x[1], reverse=True)[0][0]
    
    # Store the mapping
    video_topic_mapping[video_id] = dominant_topic
    
    # Increase count for that topic
    topic_video_count[dominant_topic] += 1

# Print number of videos assigned to each topic
print("\nNumber of Videos per Topic:")
for topic, count in sorted(topic_video_count.items()):
    print(f"Topic {topic}: {count} videos")



Number of Videos per Topic:
Topic 0: 17 videos
Topic 1: 14 videos
Topic 2: 17 videos
Topic 3: 3 videos
Topic 4: 8 videos
Topic 5: 7 videos
Topic 6: 15 videos
Topic 7: 2 videos
Topic 8: 9 videos
Topic 9: 8 videos


In [15]:
topic_to_videos = defaultdict(list)

video_topic_mapping = {}

# probability threshold for assigning multiple topics
prob_threshold = 0.2

# Dictionary to store topic words for each video
video_topic_words_LDA1 = {}

for idx, doc_bow in enumerate(corpus):
    video_id = video_ids[idx]  # Get video ID
    topic_distribution = lda_model.get_document_topics(doc_bow, minimum_probability=0)

    # Get topics where probability is above threshold
    assigned_topics = [topic for topic, prob in topic_distribution if prob >= prob_threshold]
    video_topic_mapping[video_id] = assigned_topics  # Store assigned topics per video

    for topic in assigned_topics:
        topic_to_videos[topic].append(video_id)

    # Get the representative words for each assigned topic
    topic_words = []
    for topic in assigned_topics:
        words = [word for word, _ in lda_model.show_topic(topic, topn=20)]  # Get top 10 words
        topic_words.append(", ".join(words))  # Convert list to string

    # Store the topic words as a string
    video_topic_words_LDA1[video_id] = "; ".join(topic_words)  # Separate topics with `;`

# Count occurrences of each topic
topic_counts = Counter()

for topics in video_topic_mapping.values():
    for topic in topics:
        topic_counts[topic] += 1

# Print the number of videos per topic
print("\nNumber of Videos Per Topic:")
for topic, count in sorted(topic_counts.items()):
    print(f"Topic {topic}: {count} videos")

# Print topics assigned per video
print("\nTopics Assigned Per Video:")
for video_id, topics in video_topic_mapping.items():
    topic_list = ', '.join(map(str, topics)) if topics else "No dominant topic"
    print(f"Video ID: {video_id} → Topics: {topic_list}")

# Print videos per topic
print("\nTop Words Per Topic:")
num_words = 30  

for topic_id in sorted(topic_to_videos.keys()): 
    top_words = lda_model.show_topic(topic_id, num_words)
    words_str = ', '.join([word for word, prob in top_words])
    print(f"Topic {topic_id}: {words_str}")



Number of Videos Per Topic:
Topic 0: 19 videos
Topic 1: 15 videos
Topic 2: 19 videos
Topic 3: 3 videos
Topic 4: 8 videos
Topic 5: 7 videos
Topic 6: 15 videos
Topic 7: 2 videos
Topic 8: 11 videos
Topic 9: 11 videos

Topics Assigned Per Video:
Video ID: --8n6A8Q6M0_$200 Luxury Beach Hotel in The Philippines ðŸ‡µðŸ‡­ → Topics: 9
Video ID: 0IMWasj76yU_Philippines Army vs Thailand Army → Topics: 4
Video ID: 1kErCqgIVMk_Tour of The House We Built in The Philippines → Topics: 1
Video ID: 2ftG8JuMzz4_Top 5 Exotic Foods in the Philippines The BRAVE MUST TRY! → Topics: 4
Video ID: 2TmagN6RhkI_VOCAL COACH REACTS - REGINE VELASQUEZ - Araw-Gabi → Topics: 1
Video ID: 3n1nspLgfd4_Balut!!!!! - Manila, Philippines - Now United → Topics: 0, 1
Video ID: 401ZvQ11euA_Did China Buy the Philippines With False Investment Promises → Topics: 3
Video ID: 4OiOwDh5lKE_Chef Kuya Joey Is Flying To The Philippines!  ðŸ‡µðŸ‡­ → Topics: 2
Video ID: 6ftiWoCJ4dM_Filipino Food In The Netherlands  Cafe Nordrick!! → Topics

In [16]:
transcript_files = []
for file_name in os.listdir(transcripts_folder_path):
    if file_name.endswith('.txt'):
        video_id = file_name.split('_captions')[0]
        video_ids.append(video_id)
        transcript_files.append((video_id, file_name)) 

# Dictionary to store LDA2 topic words for each video
video_topics = {}
video_topic_words_lda2 = {}
video_segments = {}  # To store segments for each video

# Create a global dictionary for LDA
dictionary = corpora.Dictionary()

# Process each video
for video_id, file_name in transcript_files:
    with open(os.path.join(transcripts_folder_path, file_name), 'r', encoding='utf-8') as file:
        content = file.read().lower()
        
        if len(content.split()) >= 100:  
            # Preprocess text and get segments
            processed_text, segments = preprocess_text(content, video_id)
            
            # Store segments for the video
            video_segments[video_id] = segments
            
            # Create Dictionary and Corpus
            tokens = processed_text.split()
            dictionary.add_documents([tokens])  # Update global dictionary
            corpus = [dictionary.doc2bow(tokens)]
            
            # Train LDA Model
            num_topics = 3  # Limit topics to at most 5 or vocab size
            lda_model_2 = LdaModel(corpus, num_topics=num_topics, id2word=dictionary, alpha='auto', eta='symmetric', passes=100)
            
            # Compute Coherence Score
            coherence_model = CoherenceModel(model=lda_model_2, corpus=corpus, dictionary=dictionary, coherence='u_mass')
            coherence_score = coherence_model.get_coherence()
            
            # Get topic distribution for the video
            topic_distribution = lda_model_2.get_document_topics(corpus[0], minimum_probability=0)
            assigned_topics = {topic: prob for topic, prob in topic_distribution if prob > 0.5}  # Threshold for multiple topics
            
            # Store video topic info
            video_topics[video_id] = {
                "topics": assigned_topics,
                "top_words": {i: lda_model_2.show_topic(i, 20) for i in range(num_topics)},
                "coherence": coherence_score
            }

# Populate video_topic_words_lda2
for video_id, data in video_topics.items():
    topic_words = []
    
    for topic_id, prob in data["topics"].items():
        words = [word for word, _ in data["top_words"][topic_id]]  # Extract top words
        topic_words.append(", ".join(words))  # Convert list to string

    # Store the topic words as a string
    video_topic_words_lda2[video_id] = "; ".join(topic_words)  # Separate topics with `;`

# Print topics per video
for video_id, data in video_topics.items():
    print(f"\nVideo ID: {video_id}")
    print(f"Coherence Score: {data['coherence']:.4f}")
    print("Assigned Topics:")
    for topic_id, prob in data["topics"].items():
        print(f"  Topic {topic_id} ({prob:.2f} probability): {[word for word, _ in data['top_words'][topic_id]]}")
    
    # Display segments for the video
    print("\nSegments:")
    for i, segment in enumerate(video_segments[video_id], 1):
        print(f"Segment {i}: {segment}")


Video ID: --8n6A8Q6M0_$200 Luxury Beach Hotel in The Philippines ðŸ‡µðŸ‡­
Coherence Score: 0.0000
Assigned Topics:
  Topic 2 (1.00 probability): ['beach', 'bum_gun', 'hotel', 'water', 'rainy_season', 'jet', 'god', 'super', 'perfect', 'ski', 'head', 'stay', 'walk', 'hour', 'sand', 'bed', 'tide', 'couple', 'fun', 'margarita']

Segments:
Segment 1: oh my god
it is just the perfect recipe for a good day
want some beer
sure
oh it's big bottle
oh my goodness
three tarzan
good morning from bohol here in the philippines
everybody guys this look
how gorgeous this place is
crystal clear water
it's just honestly such a vibe perfect
temperature to be spending the day by the beach
and that is exactly what we're gonna do
today because i'm staying about 200 meters
up that way at a $200 per night hotel
on there for the next couple of nights
and i arrived in the uh last night
uh it was raining
it was kind of a little bit miserable
so i was like you know what
we'll wait until the weather is good and bo

In [17]:
import pandas as pd
import re

def extract_video_id(url):
    """Extracts the 11-character YouTube video ID from a URL."""
    match = re.search(r"(?:v=|\/(?:embed|shorts|v)\/|youtu\.be\/)([0-9A-Za-z_-]{11})", str(url))
    return match.group(1) if match else None

def match_topics(video_id, topic_dict):
    """Matches video ID with topic dictionary keys."""
    if video_id:
        for key in topic_dict.keys():
            if key.startswith(video_id):  # Video ID matches the key prefix
                return topic_dict[key]
    return None

# Load CSV
csv_file = "topics_per_video.csv"
topics_per_video_df = pd.read_csv(csv_file)

# Extract Video ID from the "Link" column
topics_per_video_df["Video_ID"] = topics_per_video_df["Link"].apply(extract_video_id)

# Update LDA1 and LDA2 Topics columns
topics_per_video_df["LDA1 Topics"] = topics_per_video_df["Video_ID"].apply(lambda vid: match_topics(vid, video_topic_words_LDA1))
topics_per_video_df["LDA2 Topics"] = topics_per_video_df["Video_ID"].apply(lambda vid: match_topics(vid, video_topic_words_lda2))

# Save the updated CSV
topics_per_video_df.to_csv("updated_topics_per_video.csv", index=False)

print("CSV successfully updated!")


CSV successfully updated!
